In [2]:
import torch
import torchvision
import os
import cv2
import numpy as np
import xml.etree.ElementTree as ET
from torch.utils.data import Dataset, DataLoader
from torchvision.models.detection.faster_rcnn import FastRCNNPredictor
from torchvision.transforms import functional as F

In [3]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Using device: cpu


In [4]:
train_dir = "D:/New download/archive/VOC2012_train_val/VOC2012_train_val"
test_dir = "D:/New download/archive/VOC2012_test/VOC2012_test"
image_dir = os.path.join(train_dir, "JPEGImages")
annotation_dir = os.path.join(train_dir, "Annotations")
image_filenames = sorted(os.listdir(image_dir))[:500]

In [5]:
class VOCDataset(Dataset):
    def __init__(self, image_filenames):
        self.image_filenames = image_filenames
        self.classes = ['__background__', 'aeroplane', 'bicycle', 'bird', 'boat', 'bottle', 'bus', 'car', 'cat', 
                        'chair', 'cow', 'diningtable', 'dog', 'horse', 'motorbike', 'person', 'pottedplant', 
                        'sheep', 'sofa', 'train', 'tvmonitor']

    def __len__(self):
        return len(self.image_filenames)

    def __getitem__(self, idx):
        image_filename = self.image_filenames[idx]
        img_path = os.path.join(image_dir, image_filename)
        ann_path = os.path.join(annotation_dir, image_filename.replace(".jpg", ".xml"))
        
        if not os.path.exists(ann_path):
            return None  

        img = cv2.imread(img_path)
        img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        img = F.to_tensor(img)  

        tree = ET.parse(ann_path)
        root = tree.getroot()
        boxes, labels = [], []

        for obj in root.findall("object"):
            label = self.classes.index(obj.find("name").text)
            bbox = obj.find("bndbox")
            xmin, ymin, xmax, ymax = [int(bbox.find(tag).text) for tag in ("xmin", "ymin", "xmax", "ymax")]
            boxes.append([xmin, ymin, xmax, ymax])
            labels.append(label)

        target = {
            'boxes': torch.tensor(boxes, dtype=torch.float32),
            'labels': torch.tensor(labels, dtype=torch.int64)
        }

        return img, target

In [ ]:
def collate_fn(batch):
    batch = [b for b in batch if b is not None]
    return tuple(zip(*batch))

dataset = VOCDataset(image_filenames)
dataloader = DataLoader(dataset, batch_size=1, shuffle=True, collate_fn=collate_fn)

In [7]:
model = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=True)
num_classes = len(dataset.classes)
in_features = model.roi_heads.box_predictor.cls_score.in_features
model.roi_heads.box_predictor = FastRCNNPredictor(in_features, num_classes)
model.to(device)

c:\Users\gouth\AppData\Local\Programs\Python\Python310\lib\site-packages\torchvision\models\_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
c:\Users\gouth\AppData\Local\Programs\Python\Python310\lib\site-packages\torchvision\models\_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=FasterRCNN_ResNet50_FPN_Weights.COCO_V1`. You can also use `weights=FasterRCNN_ResNet50_FPN_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)


FasterRCNN(
  (transform): GeneralizedRCNNTransform(
      Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
      Resize(min_size=(800,), max_size=1333, mode='bilinear')
  )
  (backbone): BackboneWithFPN(
    (body): IntermediateLayerGetter(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): FrozenBatchNorm2d(64, eps=0.0)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): FrozenBatchNorm2d(64, eps=0.0)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): FrozenBatchNorm2d(64, eps=0.0)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): FrozenBatchNorm2d(256, eps=0.0)
          (relu): ReLU(

In [8]:
optimizer = torch.optim.SGD(model.parameters(), lr=0.005, momentum=0.9, weight_decay=0.0005)
num_epochs = 5
checkpoint_path = "model_checkpoint.pth"

if os.path.exists(checkpoint_path):
    model.load_state_dict(torch.load(checkpoint_path))
    print("Loaded checkpoint")

for epoch in range(num_epochs):
    model.train()
    total_loss = 0

    for batch_idx, (images, targets) in enumerate(dataloader):
        images = [img.to(device) for img in images]
        targets = [{k: v.to(device) for k, v in t.items()} for t in targets]

        optimizer.zero_grad()
        loss_dict = model(images, targets)
        loss = sum(loss for loss in loss_dict.values())
        loss.backward()
        optimizer.step()

        total_loss += loss.item()
        print(f"Batch {batch_idx+1}/{len(dataloader)} - Loss: {loss.item():.4f}")

    print(f"Epoch {epoch+1} - Total Loss: {total_loss:.4f}")

    if (epoch + 1) % 2 == 0:
        torch.save(model.state_dict(), checkpoint_path)
        print(f"Model checkpoint saved at epoch {epoch+1}")

torch.save(model.state_dict(), "objectdetection_model.pth")
print("🎉 Training Complete! Model saved as 'objectdetection_model.pth'")

Batch 1/500 - Loss: 3.3085
Batch 2/500 - Loss: 3.1905
Batch 3/500 - Loss: 1.0270
Batch 4/500 - Loss: 0.2609
Batch 5/500 - Loss: 1.4213
Batch 6/500 - Loss: 0.3054
Batch 7/500 - Loss: 2.6878
Batch 8/500 - Loss: 0.5472
Batch 9/500 - Loss: 0.3734
Batch 10/500 - Loss: 0.2750
Batch 11/500 - Loss: 0.3269
Batch 12/500 - Loss: 0.6221
Batch 13/500 - Loss: 2.1492
Batch 14/500 - Loss: 0.7095
Batch 15/500 - Loss: 1.5102
Batch 16/500 - Loss: 0.5892
Batch 17/500 - Loss: 0.6129
Batch 18/500 - Loss: 0.3469
Batch 19/500 - Loss: 0.9954
Batch 20/500 - Loss: 0.3992
Batch 21/500 - Loss: 0.3185
Batch 22/500 - Loss: 1.3941
Batch 23/500 - Loss: 0.4153
Batch 24/500 - Loss: 1.0522
Batch 25/500 - Loss: 0.5917
Batch 26/500 - Loss: 0.8474
Batch 27/500 - Loss: 0.3330
Batch 28/500 - Loss: 0.2826
Batch 29/500 - Loss: 0.2402
Batch 30/500 - Loss: 0.1679
Batch 31/500 - Loss: 0.5174
Batch 32/500 - Loss: 0.2082
Batch 33/500 - Loss: 0.4365
Batch 34/500 - Loss: 1.2866
Batch 35/500 - Loss: 0.8272
Batch 36/500 - Loss: 0.3018
B